### Dependencies

In [1]:
import pandas as pd

#for preprocessing
import re
import spacy
import pandas as pd
from langdetect import detect
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer

# Load NLP model
nlp = spacy.load("en_core_web_sm")

# Initialize stopwords and lemmatizer
stop_words = set(stopwords.words("english"))
lemmatizer = WordNetLemmatizer()

### Load Data

In [2]:
jobDf = pd.read_csv('postings.csv', nrows=10000)
print(jobDf.shape)
jobDf.head(3)

(10000, 31)


job_id            company_name                              title  \
0    921716   Corcoran Sawyer Smith              Marketing Coordinator   
1   1829192                     NaN  Mental Health Therapist/Counselor   
2  10998357  The National Exemplar         Assitant Restaurant Manager   

                                         description  max_salary pay_period  \
0  Job descriptionA leading real estate firm in N...        20.0     HOURLY   
1  At Aspen Therapy and Wellness , we are committ...        50.0     HOURLY   
2  The National Exemplar is accepting application...     65000.0     YEARLY   

           location  company_id  views  med_salary  ...  \
0     Princeton, NJ   2774458.0   20.0         NaN  ...   
1  Fort Collins, CO         NaN    1.0         NaN  ...   
2    Cincinnati, OH  64896719.0    8.0         NaN  ...   

                                         skills_desc   listed_time  \
0  Requirements: \n\nWe are seeking a College or ...  1.713398e+12   
1                                                NaN  1.712858e+12   
2  We are currently accepting resumes for FOH - A...  1.713278e+12   

   posting_domain  sponsored  work_type currency compensation_type  \
0             NaN          0  FULL_TIME      USD       BASE_SALARY   
1             NaN          0  FULL_TIME      USD       BASE_SALARY   
2             NaN          0  FULL_TIME      USD       BASE_SALARY   

  normalized_salary  zip_code     fips  
0           38480.0    8540.0  34021.0  
1           83200.0   80521.0   8069.0  
2           55000.0   45202.0  39061.0  

[3 rows x 31 columns]

In [3]:
resumeDf = pd.read_csv('Resume.csv')
print(resumeDf.shape)
resumeDf.head(3)

(2484, 4)


ID                                         Resume_str  \
0  16852973           HR ADMINISTRATOR/MARKETING ASSOCIATE\...   
1  22323967           HR SPECIALIST, US HR OPERATIONS      ...   
2  33176873           HR DIRECTOR       Summary      Over 2...   

                                         Resume_html Category  
0  <div class="fontsize fontface vmargins hmargin...       HR  
1  <div class="fontsize fontface vmargins hmargin...       HR  
2  <div class="fontsize fontface vmargins hmargin...       HR

### Preprocessing

In [4]:
# Text cleaning functions
def to_lowercase(text):
    return text.lower()

def keep_only_english(text):
    try:
        return text if detect(text) == 'en' else ''
    except:
        return ''

def remove_urls_emails_html(text):
    text = re.sub(r"http[s]?://\S+", "", text)  # URLs
    text = re.sub(r"\S+@\S+", "", text)  # Emails
    text = re.sub(r"<.*?>", "", text)  # HTML Tags
    return text

def remove_special_characters(text):
    return re.sub(r"[^\w\s]", "", text)

def remove_linebreaks_whitespace(text):
    text = re.sub(r"\r|\n", " ", text)  # Replace newlines
    text = re.sub(r"\s+", " ", text)  # Remove extra spaces
    return text.strip()

def remove_stopwords(text):
    return " ".join(word for word in text.split() if word not in stop_words)

def lemmatize_text(text):
    return " ".join(lemmatizer.lemmatize(word) for word in text.split())

# **Main Cleaning Function**
def clean_text(text):
    text = to_lowercase(text)
    text = keep_only_english(text)
    text = remove_urls_emails_html(text)
    text = remove_special_characters(text)
    text = remove_linebreaks_whitespace(text)
    text = remove_stopwords(text)
    text = lemmatize_text(text)
    return text

In [5]:
# Apply to job descriptions and resumes
jobDf["cleaned_text"] = jobDf["description"].apply(clean_text)
resumeDf["cleaned_text"] = resumeDf["Resume_str"].apply(clean_text)

In [6]:
def tokenize_text(text):
    doc = nlp(text)
    return [token.text for token in doc]

# Apply tokenization separately
jobDf["tokenized_text"] = jobDf["cleaned_text"].apply(tokenize_text)
resumeDf["tokenized_text"] = resumeDf["cleaned_text"].apply(tokenize_text)

In [7]:
jobDf.head(5)

job_id            company_name  \
0    921716   Corcoran Sawyer Smith   
1   1829192                     NaN   
2  10998357  The National Exemplar    
3  23221523  Abrams Fensterman, LLP   
4  35982263                     NaN   

                                               title  \
0                              Marketing Coordinator   
1                  Mental Health Therapist/Counselor   
2                        Assitant Restaurant Manager   
3  Senior Elder Law / Trusts and Estates Associat...   
4                                 Service Technician   

                                         description  max_salary pay_period  \
0  Job descriptionA leading real estate firm in N...        20.0     HOURLY   
1  At Aspen Therapy and Wellness , we are committ...        50.0     HOURLY   
2  The National Exemplar is accepting application...     65000.0     YEARLY   
3  Senior Associate Attorney - Elder Law / Trusts...    175000.0     YEARLY   
4  Looking for HVAC service tech with experience ...     80000.0     YEARLY   

            location  company_id  views  med_salary  ...  posting_domain  \
0      Princeton, NJ   2774458.0   20.0         NaN  ...             NaN   
1   Fort Collins, CO         NaN    1.0         NaN  ...             NaN   
2     Cincinnati, OH  64896719.0    8.0         NaN  ...             NaN   
3  New Hyde Park, NY    766262.0   16.0         NaN  ...             NaN   
4     Burlington, IA         NaN    3.0         NaN  ...             NaN   

  sponsored  work_type  currency  compensation_type normalized_salary  \
0         0  FULL_TIME       USD        BASE_SALARY           38480.0   
1         0  FULL_TIME       USD        BASE_SALARY           83200.0   
2         0  FULL_TIME       USD        BASE_SALARY           55000.0   
3         0  FULL_TIME       USD        BASE_SALARY          157500.0   
4         0  FULL_TIME       USD        BASE_SALARY           70000.0   

  zip_code     fips                                       cleaned_text  \
0   8540.0  34021.0  job descriptiona leading real estate firm new ...   
1  80521.0   8069.0  aspen therapy wellness committed serving clien...   
2  45202.0  39061.0  national exemplar accepting application assist...   
3  11040.0  36059.0  senior associate attorney elder law trust esta...   
4  52601.0  19057.0  looking hvac service tech experience commerica...   

                                      tokenized_text  
0  [job, descriptiona, leading, real, estate, fir...  
1  [aspen, therapy, wellness, committed, serving,...  
2  [national, exemplar, accepting, application, a...  
3  [senior, associate, attorney, elder, law, trus...  
4  [looking, hvac, service, tech, experience, com...  

[5 rows x 33 columns]

In [8]:
resumeDf.head(5)

ID                                         Resume_str  \
0  16852973           HR ADMINISTRATOR/MARKETING ASSOCIATE\...   
1  22323967           HR SPECIALIST, US HR OPERATIONS      ...   
2  33176873           HR DIRECTOR       Summary      Over 2...   
3  27018550           HR SPECIALIST       Summary    Dedica...   
4  17812897           HR MANAGER         Skill Highlights  ...   

                                         Resume_html Category  \
0  <div class="fontsize fontface vmargins hmargin...       HR   
1  <div class="fontsize fontface vmargins hmargin...       HR   
2  <div class="fontsize fontface vmargins hmargin...       HR   
3  <div class="fontsize fontface vmargins hmargin...       HR   
4  <div class="fontsize fontface vmargins hmargin...       HR   

                                        cleaned_text  \
0  hr administratormarketing associate hr adminis...   
1  hr specialist u hr operation summary versatile...   
2  hr director summary 20 year experience recruit...   
3  hr specialist summary dedicated driven dynamic...   
4  hr manager skill highlight hr skill hr departm...   

                                      tokenized_text  
0  [hr, administratormarketing, associate, hr, ad...  
1  [hr, specialist, u, hr, operation, summary, ve...  
2  [hr, director, summary, 20, year, experience, ...  
3  [hr, specialist, summary, dedicated, driven, d...  
4  [hr, manager, skill, highlight, hr, skill, hr,...

### Remove repetitive technical words

In [12]:
from sklearn.feature_extraction.text import TfidfVectorizer
vectorizer = TfidfVectorizer()


# Fit and transform the cleaned job descriptions
tfidf_matrix = vectorizer.fit_transform(jobDf["cleaned_text"])

# Create a DataFrame with words as columns
tfidf_df = pd.DataFrame(tfidf_matrix.toarray(), columns=vectorizer.get_feature_names_out())

# Sum the TF-IDF scores for each term across all job descriptions
term_tfidf = tfidf_df.sum(axis=0)

# Convert to DataFrame and sort by highest TF-IDF value
sorted_tfidf = pd.DataFrame(term_tfidf, columns=["TF-IDF"]).sort_values(by="TF-IDF", ascending=False)

                 TF-IDF
experience   303.652688
work         301.182849
customer     300.480071
team         281.605571
patient      276.989266
care         263.498670
service      255.888580
sale         235.233404
business     231.613731
client       221.050361
job          207.680722
company      200.732368
skill        199.774377
opportunity  190.502375
ability      190.266568
including    185.471066
project      185.195426
position     180.654448
management   180.067218
product      179.714386


In [24]:
# Display the top terms
sorted_tfidf.head(60)

TF-IDF
experience     303.652688
work           301.182849
customer       300.480071
team           281.605571
patient        276.989266
care           263.498670
service        255.888580
sale           235.233404
business       231.613731
client         221.050361
job            207.680722
company        200.732368
skill          199.774377
opportunity    190.502375
ability        190.266568
including      185.471066
project        185.195426
position       180.654448
management     180.067218
product        179.714386
employee       176.622337
support        169.993397
required       169.304786
year           168.915326
health         164.843038
benefit        162.203646
program        160.190947
data           159.871127
role           159.358097
system         153.046728
process        150.089620
medical        147.843407
must           145.813503
time           145.558808
information    144.790773
nursing        143.751669
requirement    142.183911
new            141.404484
need           138.380727
development    137.670456
plan           134.520979
working        133.440520
status         133.099676
financial      132.787662
knowledge      132.558299
environment    129.038445
employment     128.824774
communication  127.300554
duty           126.152410
quality        126.149892
may            125.497170
training       124.845225
professional   124.009068
store          123.700547
manager        123.254860
associate      123.073628
ensure         120.969731
provide        119.515783
life           119.241374
design         118.838302

In [26]:
# Derived from highest occuring words
words_to_remove = [
    "experience", "work", "team", "care", "service", "business", "client", "job", 
    "company", "skill", "opportunity", "ability", "including", "position", 
    "product", "employee", "support", "required", "year", "benefit", 
    "program", "data", "role", "system", "process", "time", "information", 
    "requirement", "new", "development", "plan", "working", "status", 
    "financial", "knowledge", "environment", "employment", "communication", "duty", 
    "quality", "training", "professional", "manager", "associate", "ensure", "provide", 
    "life", "design"]

In [27]:
# Function to remove specified words from tokenized text
def remove_words(tokens):
    return [word for word in tokens if word not in words_to_remove]

# Apply the function to remove the words from job and resume data
jobDf["cleaned_tokenized_text"] = jobDf["tokenized_text"].apply(remove_words)
resumeDf["cleaned_tokenized_text"] = resumeDf["tokenized_text"].apply(remove_words)

(     job_id            company_name  \
 0    921716   Corcoran Sawyer Smith   
 1   1829192                     NaN   
 2  10998357  The National Exemplar    
 3  23221523  Abrams Fensterman, LLP   
 4  35982263                     NaN   
 
                                                title  \
 0                              Marketing Coordinator   
 1                  Mental Health Therapist/Counselor   
 2                        Assitant Restaurant Manager   
 3  Senior Elder Law / Trusts and Estates Associat...   
 4                                 Service Technician   
 
                                          description  max_salary pay_period  \
 0  Job descriptionA leading real estate firm in N...        20.0     HOURLY   
 1  At Aspen Therapy and Wellness , we are committ...        50.0     HOURLY   
 2  The National Exemplar is accepting application...     65000.0     YEARLY   
 3  Senior Associate Attorney - Elder Law / Trusts...    175000.0     YEARLY   
 4  Looking fo

In [30]:
jobDf.head(3)

job_id            company_name                              title  \
0    921716   Corcoran Sawyer Smith              Marketing Coordinator   
1   1829192                     NaN  Mental Health Therapist/Counselor   
2  10998357  The National Exemplar         Assitant Restaurant Manager   

                                         description  max_salary pay_period  \
0  Job descriptionA leading real estate firm in N...        20.0     HOURLY   
1  At Aspen Therapy and Wellness , we are committ...        50.0     HOURLY   
2  The National Exemplar is accepting application...     65000.0     YEARLY   

           location  company_id  views  med_salary  ...  sponsored  work_type  \
0     Princeton, NJ   2774458.0   20.0         NaN  ...          0  FULL_TIME   
1  Fort Collins, CO         NaN    1.0         NaN  ...          0  FULL_TIME   
2    Cincinnati, OH  64896719.0    8.0         NaN  ...          0  FULL_TIME   

   currency  compensation_type  normalized_salary zip_code     fips  \
0       USD        BASE_SALARY            38480.0   8540.0  34021.0   
1       USD        BASE_SALARY            83200.0  80521.0   8069.0   
2       USD        BASE_SALARY            55000.0  45202.0  39061.0   

                                        cleaned_text  \
0  job descriptiona leading real estate firm new ...   
1  aspen therapy wellness committed serving clien...   
2  national exemplar accepting application assist...   

                                      tokenized_text  \
0  [job, descriptiona, leading, real, estate, fir...   
1  [aspen, therapy, wellness, committed, serving,...   
2  [national, exemplar, accepting, application, a...   

                              cleaned_tokenized_text  
0  [descriptiona, leading, real, estate, firm, je...  
1  [aspen, therapy, wellness, committed, serving,...  
2  [national, exemplar, accepting, application, a...  

[3 rows x 34 columns]

In [31]:
resumeDf.head(3)

ID                                         Resume_str  \
0  16852973           HR ADMINISTRATOR/MARKETING ASSOCIATE\...   
1  22323967           HR SPECIALIST, US HR OPERATIONS      ...   
2  33176873           HR DIRECTOR       Summary      Over 2...   

                                         Resume_html Category  \
0  <div class="fontsize fontface vmargins hmargin...       HR   
1  <div class="fontsize fontface vmargins hmargin...       HR   
2  <div class="fontsize fontface vmargins hmargin...       HR   

                                        cleaned_text  \
0  hr administratormarketing associate hr adminis...   
1  hr specialist u hr operation summary versatile...   
2  hr director summary 20 year experience recruit...   

                                      tokenized_text  \
0  [hr, administratormarketing, associate, hr, ad...   
1  [hr, specialist, u, hr, operation, summary, ve...   
2  [hr, director, summary, 20, year, experience, ...   

                              cleaned_tokenized_text  
0  [hr, administratormarketing, hr, administrator...  
1  [hr, specialist, u, hr, operation, summary, ve...  
2  [hr, director, summary, 20, recruiting, 15, pl...

### tokens embedding (all-MiniLM-L6-v2, roberta-base-nli, JobBert)

In [49]:
pip install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu121

Looking in indexes: https://download.pytorch.org/whl/cu121
     ---------------------------------------- 0.0/6.1 MB ? eta -:--:--
     ---------------------------------------- 0.0/6.1 MB ? eta -:--:--
     ---------------------------------------- 0.0/6.1 MB ? eta -:--:--
     - -------------------------------------- 0.3/6.1 MB ? eta -:--:--
     --- ------------------------------------ 0.5/6.1 MB 1.3 MB/s eta 0:00:05
     ----- ---------------------------------- 0.8/6.1 MB 1.4 MB/s eta 0:00:04
     -------- ------------------------------- 1.3/6.1 MB 1.7 MB/s eta 0:00:03
     ---------- ----------------------------- 1.6/6.1 MB 1.7 MB/s eta 0:00:03
     ------------- -------------------------- 2.1/6.1 MB 1.7 MB/s eta 0:00:03
     --------------- ------------------------ 2.4/6.1 MB 1.8 MB/s eta 0:00:03
     ------------------- -------------------- 2.9/6.1 MB 1.9 MB/s eta 0:00:02
     ---------------------- ----------------- 3.4/6.1 MB 2.0 MB/s eta 0:00:02
     ------------------------- --

  You can safely remove it manually.


In [32]:
from sentence_transformers import SentenceTransformer
import torch
from tqdm import tqdm

# Load the model
model_miniLM = SentenceTransformer('all-MiniLM-L6-v2')

# Ensure we're using GPU if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model_miniLM = model_miniLM.to(device)

# Create a function to get embeddings
def get_miniLM_embeddings(texts):
    return model_miniLM.encode(texts, show_progress_bar=True, device=device)

# Get embeddings for both jobs and resumes
job_embeddings_miniLM = []
for job_description in tqdm(jobDf["cleaned_text"], desc="Processing job descriptions with MiniLM"):
    job_embeddings_miniLM.append(get_miniLM_embeddings([job_description]))

resume_embeddings_miniLM = []
for resume in tqdm(resumeDf["cleaned_text"], desc="Processing resumes with MiniLM"):
    resume_embeddings_miniLM.append(get_miniLM_embeddings([resume]))

# Add the embeddings to the dataframe
jobDf["miniLM_embeddings"] = job_embeddings_miniLM
resumeDf["miniLM_embeddings"] = resume_embeddings_miniLM


Processing job descriptions with MiniLM:   0%|                                               | 0/10000 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Processing job descriptions with MiniLM:   0%|                                     | 1/10000 [00:00<1:33:19,  1.79it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Processing job descriptions with MiniLM:   0%|                                       | 2/10000 [00:00<56:31,  2.95it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Processing resumes with MiniLM: 100%|█████████████████████████████████████████████▉| 2483/2484 [02:06<00:00, 20.32it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Processing resumes with MiniLM: 100%|██████████████████████████████████████████████| 2484/2484 [02:06<00:00, 19.63it/s]


In [50]:
# from transformers import AutoTokenizer, AutoModel

# # Load the model and tokenizer
# tokenizer_roberta = AutoTokenizer.from_pretrained('roberta-base-nli')
# model_roberta = AutoModel.from_pretrained('roberta-base-nli')

# # Ensure we're using GPU if available
# device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# model_roberta = model_roberta.to(device)

# # Create a function to get embeddings
# def get_roberta_embeddings(texts):
#     inputs = tokenizer_roberta(texts, padding=True, truncation=True, return_tensors="pt", max_length=512).to(device)
#     with torch.no_grad():
#         outputs = model_roberta(**inputs)
#     return outputs.last_hidden_state[:, 0].cpu().numpy()  # CLS token for sentence embedding

# # Get embeddings for both jobs and resumes
# job_embeddings_roberta = []
# for job_description in tqdm(jobDf["cleaned_text"], desc="Processing job descriptions with RoBERTa"):
#     job_embeddings_roberta.append(get_roberta_embeddings([job_description]))

# resume_embeddings_roberta = []
# for resume in tqdm(resumeDf["cleaned_text"], desc="Processing resumes with RoBERTa"):
#     resume_embeddings_roberta.append(get_roberta_embeddings([resume]))

# # Add the embeddings to the dataframe
# jobDf["roberta_embeddings"] = job_embeddings_roberta
# resumeDf["roberta_embeddings"] = resume_embeddings_roberta


OSError: roberta-base-nli is not a local folder and is not a valid model identifier listed on 'https://huggingface.co/models'
If this is a private repository, make sure to pass a token having permission to this repo either by logging in with `huggingface-cli login` or by passing `token=<your_token>`

In [36]:
# # Load the JobBert model and tokenizer
# tokenizer_jobBert = AutoTokenizer.from_pretrained('JobBERT')
# model_jobBert = AutoModel.from_pretrained('JobBERT')

# # Ensure we're using GPU if available
# device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
# model_jobBert = model_jobBert.to(device)

# # Create a function to get embeddings
# def get_jobBert_embeddings(texts):
#     inputs = tokenizer_jobBert(texts, padding=True, truncation=True, return_tensors="pt", max_length=512).to(device)
#     with torch.no_grad():
#         outputs = model_jobBert(**inputs)
#     return outputs.last_hidden_state[:, 0].cpu().numpy()  # CLS token for sentence embedding

# # Get embeddings for both jobs and resumes
# job_embeddings_jobBert = []
# for job_description in tqdm(jobDf["cleaned_text"], desc="Processing job descriptions with JobBERT"):
#     job_embeddings_jobBert.append(get_jobBert_embeddings([job_description]))

# resume_embeddings_jobBert = []
# for resume in tqdm(resumeDf["cleaned_text"], desc="Processing resumes with JobBERT"):
#     resume_embeddings_jobBert.append(get_jobBert_embeddings([resume]))

# # Add the embeddings to the dataframe
# jobDf["jobBert_embeddings"] = job_embeddings_jobBert
# resumeDf["jobBert_embeddings"] = resume_embeddings_jobBert


In [37]:
jobDf

job_id            company_name  \
0         921716   Corcoran Sawyer Smith   
1        1829192                     NaN   
2       10998357  The National Exemplar    
3       23221523  Abrams Fensterman, LLP   
4       35982263                     NaN   
...          ...                     ...   
9995  3886863612         The Job Network   
9996  3886863627                Revature   
9997  3886863633         The Job Network   
9998  3886863634         The Job Network   
9999  3886863643         The Job Network   

                                                  title  \
0                                 Marketing Coordinator   
1                     Mental Health Therapist/Counselor   
2                           Assitant Restaurant Manager   
3     Senior Elder Law / Trusts and Estates Associat...   
4                                    Service Technician   
...                                                 ...   
9995               Physical Therapist (PT) / Broomfield   
9996                    Entry-Level Automotive Engineer   
9997                              Automation Technician   
9998                                 Service Technician   
9999  Machine Operators; Louisa - Urgently Hiring al...   

                                            description  max_salary  \
0     Job descriptionA leading real estate firm in N...        20.0   
1     At Aspen Therapy and Wellness , we are committ...        50.0   
2     The National Exemplar is accepting application...     65000.0   
3     Senior Associate Attorney - Elder Law / Trusts...    175000.0   
4     Looking for HVAC service tech with experience ...     80000.0   
...                                                 ...         ...   
9995  Home Health Physical Therapist (PT)\n\nLocatio...    120000.0   
9996  About the RoleIn today's automotive landscape,...         NaN   
9997  Summary\n\nPer Se is currently seeking an Entr...         NaN   
9998  Pay: $18.50-30 Per Hour DOE\n\nLocation: Lovel...        30.0   
9999  We are hiring Machine Operators - and Material...        18.0   

     pay_period                   location  company_id  views  med_salary  \
0        HOURLY              Princeton, NJ   2774458.0   20.0         NaN   
1        HOURLY           Fort Collins, CO         NaN    1.0         NaN   
2        YEARLY             Cincinnati, OH  64896719.0    8.0         NaN   
3        YEARLY          New Hyde Park, NY    766262.0   16.0         NaN   
4        YEARLY             Burlington, IA         NaN    3.0         NaN   
...         ...                        ...         ...    ...         ...   
9995     YEARLY             Broomfield, CO    167757.0    3.0         NaN   
9996        NaN  California, United States  10510386.0    3.0         NaN   
9997        NaN            Minneapolis, MN    167757.0    4.0         NaN   
9998     HOURLY               Loveland, CO    167757.0    4.0         NaN   
9999     HOURLY                 Louisa, VA    167757.0    5.0         NaN   

      ...  work_type currency  compensation_type  normalized_salary  zip_code  \
0     ...  FULL_TIME      USD        BASE_SALARY            38480.0    8540.0   
1     ...  FULL_TIME      USD        BASE_SALARY            83200.0   80521.0   
2     ...  FULL_TIME      USD        BASE_SALARY            55000.0   45202.0   
3     ...  FULL_TIME      USD        BASE_SALARY           157500.0   11040.0   
4     ...  FULL_TIME      USD        BASE_SALARY            70000.0   52601.0   
...   ...        ...      ...                ...                ...       ...   
9995  ...  FULL_TIME      USD        BASE_SALARY           108500.0   80020.0   
9996  ...  FULL_TIME      NaN                NaN                NaN       NaN   
9997  ...  FULL_TIME      NaN                NaN                NaN   55401.0   
9998  ...  FULL_TIME      USD        BASE_SALARY            50440.0   80537.0   
9999  ...  FULL_TIME      USD        BASE_SALARY            34320.0   23093.0   

         fips        

In [38]:
resumeDf

ID                                         Resume_str  \
0     16852973           HR ADMINISTRATOR/MARKETING ASSOCIATE\...   
1     22323967           HR SPECIALIST, US HR OPERATIONS      ...   
2     33176873           HR DIRECTOR       Summary      Over 2...   
3     27018550           HR SPECIALIST       Summary    Dedica...   
4     17812897           HR MANAGER         Skill Highlights  ...   
...        ...                                                ...   
2479  99416532           RANK: SGT/E-5 NON- COMMISSIONED OFFIC...   
2480  24589765           GOVERNMENT RELATIONS, COMMUNICATIONS ...   
2481  31605080           GEEK SQUAD AGENT         Professional...   
2482  21190805           PROGRAM DIRECTOR / OFFICE MANAGER    ...   
2483  37473139           STOREKEEPER II       Professional Sum...   

                                            Resume_html  Category  \
0     <div class="fontsize fontface vmargins hmargin...        HR   
1     <div class="fontsize fontface vmargins hmargin...        HR   
2     <div class="fontsize fontface vmargins hmargin...        HR   
3     <div class="fontsize fontface vmargins hmargin...        HR   
4     <div class="fontsize fontface vmargins hmargin...        HR   
...                                                 ...       ...   
2479  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2480  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2481  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2482  <div class="fontsize fontface vmargins hmargin...  AVIATION   
2483  <div class="fontsize fontface vmargins hmargin...  AVIATION   

                                           cleaned_text  \
0     hr administratormarketing associate hr adminis...   
1     hr specialist u hr operation summary versatile...   
2     hr director summary 20 year experience recruit...   
3     hr specialist summary dedicated driven dynamic...   
4     hr manager skill highlight hr skill hr departm...   
...                                                 ...   
2479  rank sgte5 non commissioned officer charge bri...   
2480  government relation communication organization...   
2481  geek squad agent professional profile support ...   
2482  program director office manager summary highly...   
2483  storekeeper ii professional summary purpose do...   

                                         tokenized_text  \
0     [hr, administratormarketing, associate, hr, ad...   
1     [hr, specialist, u, hr, operation, summary, ve...   
2     [hr, director, summary, 20, year, experience, ...   
3     [hr, specialist, summary, dedicated, driven, d...   
4     [hr, manager, skill, highlight, hr, skill, hr,...   
...                                                 ...   
2479  [rank, sgte5, non, commissioned, officer, char...   
2480  [government, relation, communication, organiza...   
2481  [geek, squad, agent, professional, profile, su...   
2482  [program, director, office, manager, summary, ...   
2483  [storekeeper, ii, professional, summary, purpo...   

                                 cleaned_tokenized_text  \
0     [hr, administratormarketing, hr, administrator...   
1     [hr, specialist, u, hr, operation, summary, ve...   
2     [hr, director, summary, 20, recruiting, 15, pl...   
3     [hr, specialist, summary, dedicated, driven, d...   
4     [hr, highlight, hr, hr, department, startup, t...   
...                                                 ...   
2479  [rank, sgte5, non, commissioned, officer, char...   
2480  [government, relation, organizational, directo...   
2481  [geek, squad, agent, profile, specialist, acro...   
2482  [director, office, summary, highly, personable...   
2483  [storekeeper, ii, summary, purpose, document, ...   

                                      miniLM_embeddings  
0     [[0.008202725, -0.018283112, -0.02552449, 0.07...  
1     [[0.013234647, -0.016297316, -0.033938825, 0.0...  
2     [[-0.03459343, 0.0013017519, -0.040863078, 0.0.

In [39]:
jobDf["miniLM_embeddings"][0]

array([[ 2.35281028e-02, -4.71276678e-02, -3.99180315e-03,
         8.46532285e-02,  1.22246137e-02, -1.65377132e-04,
        -4.55360487e-02, -5.64149320e-02, -3.86138372e-02,
        -3.63909528e-02, -2.53453329e-02, -6.00324161e-02,
        -6.21968135e-03, -2.85036620e-02,  5.69380224e-02,
         4.68036020e-03,  8.52397382e-02,  1.40297674e-02,
        -7.05116466e-02,  2.70193424e-02, -1.28175784e-03,
        -2.13758815e-02, -4.08137739e-02, -9.27909836e-02,
        -3.89039554e-02, -7.17107654e-02,  2.44839992e-02,
         3.22455056e-02, -4.45699506e-02, -8.34468827e-02,
        -1.05757378e-02,  1.11636005e-01,  7.71730095e-02,
         7.94228464e-02,  7.20334426e-02,  7.66158476e-02,
        -8.94727260e-02,  9.18907970e-02,  7.95900822e-02,
        -4.16736230e-02, -1.16479121e-01, -7.02721849e-02,
        -4.56939228e-02, -2.37791110e-02,  2.60763504e-02,
        -8.89034420e-02, -4.50801216e-02, -6.58164471e-02,
         1.09859230e-02,  2.38728877e-02, -9.82307643e-0

In [53]:
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.neighbors import NearestNeighbors
from scipy.spatial.distance import euclidean

# Choose a specific job from jobDf
job_id = 921716  # Example job id
job = jobDf.loc[jobDf['job_id'] == job_id]

# Get the embedding of the selected job (flatten the list of lists)
job_embedding = np.array(job['miniLM_embeddings'].values[0]).flatten()

# Get all resume embeddings (flatten the list of lists)
resume_embeddings = np.vstack([np.array(resume).flatten() for resume in resumeDf['miniLM_embeddings'].values])

# 1. **Cosine Similarity** - Compute similarity between job and all resumes
cosine_similarities = cosine_similarity([job_embedding], resume_embeddings)
top_indices_cosine = cosine_similarities[0].argsort()[-3:][::-1]  # Top 3 most similar

# Print the job description
print("Job Description:\n", job['description'].values[0])

# Print the top 3 recommended resumes based on Cosine Similarity
print("\nTop 3 Recommended Resumes based on Cosine Similarity:")
for idx in top_indices_cosine:
    print(f"Resume ID: {resumeDf.iloc[idx]['ID']}")
    print(f"Resume Text: {resumeDf.iloc[idx]['Resume_str']}\n")

# 2. **ANN (Approximate Nearest Neighbors)** - Use NearestNeighbors to find nearest resumes
nn_model = NearestNeighbors(n_neighbors=3, metric='cosine')
nn_model.fit(resume_embeddings)
_, top_indices_ann = nn_model.kneighbors([job_embedding])

# Print the top 3 recommended resumes based on ANN
print("\nTop 3 Recommended Resumes based on ANN:")
for idx in top_indices_ann[0]:
    print(f"Resume ID: {resumeDf.iloc[idx]['ID']}")
    print(f"Resume Text: {resumeDf.iloc[idx]['Resume_str']}\n")

# 3. **Euclidean Distance** - Compute Euclidean distance between job and all resumes
distances = [euclidean(job_embedding, resume) for resume in resume_embeddings]
top_indices_euclidean = np.argsort(distances)[:3]  # Top 3 closest resumes

# Print the top 3 recommended resumes based on Euclidean Distance
print("\nTop 3 Recommended Resumes based on Euclidean Distance:")
for idx in top_indices_euclidean:
    print(f"Resume ID: {resumeDf.iloc[idx]['ID']}")
    print(f"Resume Text: {resumeDf.iloc[idx]['Resume_str']}\n")

Job Description:
 Job descriptionA leading real estate firm in New Jersey is seeking an administrative Marketing Coordinator with some experience in graphic design. You will be working closely with our fun, kind, ambitious members of the sales team and our dynamic executive team on a daily basis. This is an opportunity to be part of a fast-growing, highly respected real estate brokerage with a reputation for exceptional marketing and extraordinary culture of cooperation and inclusion.Who you are:You must be a well-organized, creative, proactive, positive, and most importantly, kind-hearted person. Please, be responsible, respectful, and cool-under-pressure. Please, be proficient in Adobe Creative Cloud (Indesign, Illustrator, Photoshop) and Microsoft Office Suite. Above all, have fantastic taste and be a good-hearted, fun-loving person who loves working with people and is eager to learn.Role:Our office is a fast-paced environment. You’ll work directly with a Marketing team and communic